In [1]:
import cv2
import numpy as np
from matplotlib.pyplot import imshow
import os
%matplotlib inline
import csv    


In [2]:
file_list =os.listdir('/home/junhyun/CT_20')

In [12]:
for threshold_value in range(0,255,5):

    for k in range(len(file_list)):
        img = cv2.imread(os.path.join('/home/junhyun/CT_20',file_list[k]))

        img_B = img[:,:,0]
        img_R = img[:,:,2]
        I_1 = img_R-img_B
        
        # threshold_value = 191
        ret, thresh = cv2.threshold(I_1, threshold_value, 255, cv2.THRESH_BINARY)
        I_2 = np.invert(thresh)


        kernel_size_row = 3
        kernel_size_col = 3
        kernel = cv2.getStructuringElement(cv2.MORPH_RECT, (kernel_size_row , kernel_size_col))

        erosion = cv2.erode(I_2,kernel,iterations=1)

        dilation = cv2.dilate(erosion,kernel,iterations=1)

        dilation = cv2.dilate(dilation,kernel,iterations=1)

        ret, dilation = cv2.threshold(dilation, 150, 255, cv2.THRESH_BINARY)

        I_3 = dilation==I_2

        _, contours, _ = cv2.findContours(dilation, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)


        original_img = img.copy()

        area_array = []
        center_array = []
        xywh_array=[]

        for cnt in contours:
            area = cv2.contourArea(cnt)

            if area > 20**2:
                x,y,w,h = cv2.boundingRect(cnt)
                #cv2.rectangle(original_img, (x,y), (x+w,y+h), (0,255,0), 2)

                area_array.append(w*h)
                center_array.append([x+w/2,y+h/2])
                xywh_array.append([x,y,w,h])
        

        # max value of area
        max_area = 0
        for area in area_array:
            if area > max_area:
                max_area = area

        del_list = []
        New_area = []
        New_center = []

        for i in range(len(area_array)):
            for j in range(i+1,len(area_array)):
                area_1 = area_array[i]
                area_2 = area_array[j]

                cnt_1_center = center_array[i]
                cnt_2_center = center_array[j]

                distance = np.sqrt((cnt_1_center[0]-cnt_2_center[0])**2+(cnt_1_center[1]-cnt_2_center[1])**2)
                union_area = area_1+area_2


                if (distance<70) and (union_area<max_area):
                    New_area.append(union_area)
                    New_center.append([(cnt_1_center[0]+cnt_2_center[0])/2,(cnt_1_center[1]+cnt_2_center[1])/2])
                    del_list.append(i)
                    del_list.append(j)

                    print('distance %d - %d : %d'%(i,j,distance))
                    print('union area %d - %d : %d'%(i,j,union_area))

        final_img = img.copy()
        
        f = open(os.path.join('/home/junhyun/TEST_threshold',str(threshold_value)+"_"+os.path.splitext(file_list[k])[0]+'.csv'), 'w', encoding='utf-8', newline='')
        wr = csv.writer(f)

        for i in range(len(area_array)):

            if i not in del_list:
                x,y,w,h = xywh_array[i]
                
                end_x = x+w
                end_y = y+h
                
                if x<0:
                    x=0
                if y<0:
                    y=0
                if end_x>img.shape[1]:
                    end_x = img.shape[1]
                if end_y>img.shape[0]:
                    end_y = img.shape[0]
                    
                
                wr.writerow(xywh_array[i])
                cv2.rectangle(final_img, (x,y), (end_x,end_y), (0,255,0), 2)


        for i in range(len(New_area)):
            area = New_area[i]
            center_x,center_y = New_center[i]
            
            w = np.sqrt(area)
            h = w
            
            if int(center_x-w/2) < 0:
                new_x = 0
                w = w + int(center_x-w/2)
            else:
                new_x = int(center_x-w/2)
                
            if int(center_y-h/2) < 0:
                new_y = 0
                h = h+int(center_y-h/2)
            else:
                new_y = int(center_y-h/2)
                
            if int(center_x+w/2) > img.shape[1]:
                new_end_x = img.shape[1]
                w = w - (int(center_x-w/2)-img.shape[1])
            else:
                new_end_x = int(center_x+w/2)
                
            if int(center_y+h/2) > img.shape[0]:
                new_end_y = img.shape[0]
                h = h - (int(center_y+h/2)-img.shape[0])
            else:
                new_end_y = int(center_y+h/2)
                
                
            
            wr.writerow([new_x,new_y,int(w),int(h)])
            
            cv2.rectangle(final_img, (new_x,new_y), (new_end_x,new_end_y), (0,255,0), 2)

        f.close()
        
              
        cv2.imwrite(os.path.join('/home/junhyun/TEST_threshold',str(threshold_value)+'_'+os.path.splitext(file_list[k])[0]+"_"+'final_img.png'), final_img)
        print(str(threshold_value)+os.path.splitext(file_list[k])[0]+"_"+'final_img.png')
        

        dual_img = img.copy()

        for i in range(len(area_array)):
            x,y,w,h = xywh_array[i]
            cv2.rectangle(dual_img, (x,y), (x+w,y+h), (0,255,0), 2)


        for i in range(len(New_area)):
            area = New_area[i]
            center_x,center_y = New_center[i]

            w = np.sqrt(area)
            h = w

            cv2.rectangle(dual_img, (int(center_x-w/2),int(center_y-h/2)), (int(center_x+w/2),int(center_y+h/2)), (0,0,255), 2)

        cv2.imwrite(os.path.join('/home/junhyun/TEST_threshold',str(threshold_value)+'_'+os.path.splitext(file_list[k])[0]+"_"+'dual_img.png'), dual_img)
        print(str(threshold_value)+os.path.splitext(file_list[k])[0]+"_"+'dual_img.png')

0TEST16_final_img.png
0TEST16_dual_img.png
0TEST26_final_img.png
0TEST26_dual_img.png
0TEST19_final_img.png
0TEST19_dual_img.png
0TEST2_final_img.png
0TEST2_dual_img.png
0TEST14_final_img.png
0TEST14_dual_img.png
0TEST4_final_img.png
0TEST4_dual_img.png
0TEST15_final_img.png
0TEST15_dual_img.png
0TEST3_final_img.png
0TEST3_dual_img.png
0TEST18_final_img.png
0TEST18_dual_img.png
0TEST17_final_img.png
0TEST17_dual_img.png
0TEST10_final_img.png
0TEST10_dual_img.png
0TEST13_final_img.png
0TEST13_dual_img.png
0TEST8_final_img.png
0TEST8_dual_img.png
0TEST23_final_img.png
0TEST23_dual_img.png
0TEST11_final_img.png
0TEST11_dual_img.png
0TEST24_final_img.png
0TEST24_dual_img.png
0TEST1_final_img.png
0TEST1_dual_img.png
0TEST22_final_img.png
0TEST22_dual_img.png
0TEST12_final_img.png
0TEST12_dual_img.png
0TEST25_final_img.png
0TEST25_dual_img.png
0TEST5_final_img.png
0TEST5_dual_img.png
0TEST27_final_img.png
0TEST27_dual_img.png
0TEST20_final_img.png
0TEST20_dual_img.png
0TEST6_final_img.png
0T

30TEST9_final_img.png
30TEST9_dual_img.png
35TEST16_final_img.png
35TEST16_dual_img.png
35TEST26_final_img.png
35TEST26_dual_img.png
35TEST19_final_img.png
35TEST19_dual_img.png
35TEST2_final_img.png
35TEST2_dual_img.png
35TEST14_final_img.png
35TEST14_dual_img.png
35TEST4_final_img.png
35TEST4_dual_img.png
35TEST15_final_img.png
35TEST15_dual_img.png
35TEST3_final_img.png
35TEST3_dual_img.png
35TEST18_final_img.png
35TEST18_dual_img.png
35TEST17_final_img.png
35TEST17_dual_img.png
35TEST10_final_img.png
35TEST10_dual_img.png
35TEST13_final_img.png
35TEST13_dual_img.png
35TEST8_final_img.png
35TEST8_dual_img.png
35TEST23_final_img.png
35TEST23_dual_img.png
35TEST11_final_img.png
35TEST11_dual_img.png
35TEST24_final_img.png
35TEST24_dual_img.png
35TEST1_final_img.png
35TEST1_dual_img.png
35TEST22_final_img.png
35TEST22_dual_img.png
35TEST12_final_img.png
35TEST12_dual_img.png
35TEST25_final_img.png
35TEST25_dual_img.png
35TEST5_final_img.png
35TEST5_dual_img.png
35TEST27_final_img.png
3

65TEST20_final_img.png
65TEST20_dual_img.png
65TEST6_final_img.png
65TEST6_dual_img.png
65TEST7_final_img.png
65TEST7_dual_img.png
65TEST21_final_img.png
65TEST21_dual_img.png
65TEST9_final_img.png
65TEST9_dual_img.png
70TEST16_final_img.png
70TEST16_dual_img.png
70TEST26_final_img.png
70TEST26_dual_img.png
70TEST19_final_img.png
70TEST19_dual_img.png
70TEST2_final_img.png
70TEST2_dual_img.png
70TEST14_final_img.png
70TEST14_dual_img.png
70TEST4_final_img.png
70TEST4_dual_img.png
70TEST15_final_img.png
70TEST15_dual_img.png
70TEST3_final_img.png
70TEST3_dual_img.png
70TEST18_final_img.png
70TEST18_dual_img.png
70TEST17_final_img.png
70TEST17_dual_img.png
70TEST10_final_img.png
70TEST10_dual_img.png
70TEST13_final_img.png
70TEST13_dual_img.png
70TEST8_final_img.png
70TEST8_dual_img.png
70TEST23_final_img.png
70TEST23_dual_img.png
70TEST11_final_img.png
70TEST11_dual_img.png
70TEST24_final_img.png
70TEST24_dual_img.png
70TEST1_final_img.png
70TEST1_dual_img.png
70TEST22_final_img.png
70T

100TEST12_final_img.png
100TEST12_dual_img.png
100TEST25_final_img.png
100TEST25_dual_img.png
100TEST5_final_img.png
100TEST5_dual_img.png
100TEST27_final_img.png
100TEST27_dual_img.png
100TEST20_final_img.png
100TEST20_dual_img.png
100TEST6_final_img.png
100TEST6_dual_img.png
100TEST7_final_img.png
100TEST7_dual_img.png
100TEST21_final_img.png
100TEST21_dual_img.png
100TEST9_final_img.png
100TEST9_dual_img.png
105TEST16_final_img.png
105TEST16_dual_img.png
105TEST26_final_img.png
105TEST26_dual_img.png
105TEST19_final_img.png
105TEST19_dual_img.png
105TEST2_final_img.png
105TEST2_dual_img.png
105TEST14_final_img.png
105TEST14_dual_img.png
105TEST4_final_img.png
105TEST4_dual_img.png
105TEST15_final_img.png
105TEST15_dual_img.png
105TEST3_final_img.png
105TEST3_dual_img.png
105TEST18_final_img.png
105TEST18_dual_img.png
105TEST17_final_img.png
105TEST17_dual_img.png
105TEST10_final_img.png
105TEST10_dual_img.png
105TEST13_final_img.png
105TEST13_dual_img.png
105TEST8_final_img.png
105T

135TEST15_final_img.png
135TEST15_dual_img.png
135TEST3_final_img.png
135TEST3_dual_img.png
135TEST18_final_img.png
135TEST18_dual_img.png
135TEST17_final_img.png
135TEST17_dual_img.png
135TEST10_final_img.png
135TEST10_dual_img.png
135TEST13_final_img.png
135TEST13_dual_img.png
135TEST8_final_img.png
135TEST8_dual_img.png
135TEST23_final_img.png
135TEST23_dual_img.png
135TEST11_final_img.png
135TEST11_dual_img.png
135TEST24_final_img.png
135TEST24_dual_img.png
135TEST1_final_img.png
135TEST1_dual_img.png
135TEST22_final_img.png
135TEST22_dual_img.png
135TEST12_final_img.png
135TEST12_dual_img.png
135TEST25_final_img.png
135TEST25_dual_img.png
135TEST5_final_img.png
135TEST5_dual_img.png
135TEST27_final_img.png
135TEST27_dual_img.png
135TEST20_final_img.png
135TEST20_dual_img.png
135TEST6_final_img.png
135TEST6_dual_img.png
135TEST7_final_img.png
135TEST7_dual_img.png
135TEST21_final_img.png
135TEST21_dual_img.png
135TEST9_final_img.png
135TEST9_dual_img.png
140TEST16_final_img.png
140

...

230TEST20_final_img.png
230TEST20_dual_img.png
distance 0 - 1 : 52
union area 0 - 1 : 1826
230TEST6_final_img.png
230TEST6_dual_img.png
distance 2 - 3 : 51
union area 2 - 3 : 5496
distance 3 - 4 : 68
union area 3 - 4 : 5009
distance 3 - 5 : 46
union area 3 - 5 : 6381
distance 4 - 5 : 26
union area 4 - 5 : 3422
distance 4 - 6 : 52
union area 4 - 6 : 2296
distance 5 - 6 : 54
union area 5 - 6 : 3668
230TEST7_final_img.png
230TEST7_dual_img.png
distance 2 - 3 : 44
union area 2 - 3 : 2289
distance 5 - 10 : 50
union area 5 - 10 : 4686
distance 5 - 16 : 56
union area 5 - 16 : 5561
distance 7 - 9 : 37
union area 7 - 9 : 7140
distance 7 - 12 : 62
union area 7 - 12 : 6350
distance 8 - 11 : 43
union area 8 - 11 : 23014
distance 9 - 14 : 56
union area 9 - 14 : 4638
distance 10 - 12 : 55
union area 10 - 12 : 6092
distance 10 - 16 : 46
union area 10 - 16 : 7805
distance 13 - 15 : 36
union area 13 - 15 : 4904
distance 13 - 18 : 36
union area 13 - 18 : 3735
distance 14 - 19 : 36
union area 14 - 19 : 2

230TEST21_final_img.png
230TEST21_dual_img.png
230TEST9_final_img.png
230TEST9_dual_img.png
235TEST16_final_img.png
235TEST16_dual_img.png
235TEST26_final_img.png
235TEST26_dual_img.png
235TEST19_final_img.png
235TEST19_dual_img.png
distance 2 - 3 : 48
union area 2 - 3 : 3649
distance 4 - 5 : 36
union area 4 - 5 : 2484
distance 6 - 7 : 52
union area 6 - 7 : 2384
distance 6 - 8 : 46
union area 6 - 8 : 1729
distance 7 - 8 : 50
union area 7 - 8 : 2855
distance 8 - 9 : 69
union area 8 - 9 : 2728
distance 9 - 11 : 61
union area 9 - 11 : 5058
distance 9 - 12 : 47
union area 9 - 12 : 3854
distance 9 - 14 : 65
union area 9 - 14 : 10128
distance 10 - 11 : 58
union area 10 - 11 : 4510
distance 10 - 13 : 61
union area 10 - 13 : 5780
distance 11 - 13 : 40
union area 11 - 13 : 8130
distance 12 - 14 : 55
union area 12 - 14 : 10726
235TEST2_final_img.png
235TEST2_dual_img.png
distance 2 - 4 : 47
union area 2 - 4 : 2372
distance 2 - 10 : 65
union area 2 - 10 : 2440
distance 4 - 7 : 52
union area 4 - 7

235TEST14_final_img.png
235TEST14_dual_img.png
235TEST4_final_img.png
235TEST4_dual_img.png
235TEST15_final_img.png
235TEST15_dual_img.png
distance 1 - 2 : 35
union area 1 - 2 : 2035
235TEST3_final_img.png
235TEST3_dual_img.png
distance 2 - 3 : 32
union area 2 - 3 : 9695
distance 2 - 4 : 61
union area 2 - 4 : 11694
distance 3 - 4 : 52
union area 3 - 4 : 4589
distance 5 - 6 : 66
union area 5 - 6 : 1628
distance 6 - 7 : 63
union area 6 - 7 : 2380
distance 6 - 9 : 43
union area 6 - 9 : 5984
distance 7 - 9 : 57
union area 7 - 9 : 6884
distance 10 - 11 : 65
union area 10 - 11 : 3340
distance 11 - 13 : 45
union area 11 - 13 : 3822
distance 12 - 13 : 64
union area 12 - 13 : 9621
distance 12 - 17 : 68
union area 12 - 17 : 9170
distance 13 - 21 : 63
union area 13 - 21 : 3641
distance 14 - 19 : 36
union area 14 - 19 : 4974
distance 15 - 16 : 63
union area 15 - 16 : 4960
distance 20 - 33 : 62
union area 20 - 33 : 12364
distance 21 - 23 : 50
union area 21 - 23 : 3161
distance 21 - 26 : 49
union ar

235TEST10_final_img.png
235TEST10_dual_img.png
235TEST13_final_img.png
235TEST13_dual_img.png
235TEST8_final_img.png
235TEST8_dual_img.png
235TEST23_final_img.png
235TEST23_dual_img.png
235TEST11_final_img.png
235TEST11_dual_img.png
235TEST24_final_img.png
235TEST24_dual_img.png
distance 0 - 1 : 62
union area 0 - 1 : 5034
235TEST1_final_img.png
235TEST1_dual_img.png
235TEST22_final_img.png
235TEST22_dual_img.png
235TEST12_final_img.png
235TEST12_dual_img.png
235TEST25_final_img.png
235TEST25_dual_img.png
distance 1 - 2 : 41
union area 1 - 2 : 1254
235TEST5_final_img.png
235TEST5_dual_img.png
235TEST27_final_img.png
235TEST27_dual_img.png
distance 1 - 2 : 45
union area 1 - 2 : 2750
distance 4 - 5 : 67
union area 4 - 5 : 2581
distance 4 - 8 : 42
union area 4 - 8 : 2743
distance 5 - 8 : 64
union area 5 - 8 : 3278
distance 6 - 9 : 60
union area 6 - 9 : 3565
distance 8 - 11 : 69
union area 8 - 11 : 3436
distance 9 - 14 : 55
union area 9 - 14 : 3786
distance 10 - 14 : 51
union area 10 - 14 :

240TEST15_final_img.png
240TEST15_dual_img.png
240TEST3_final_img.png
240TEST3_dual_img.png
distance 0 - 1 : 66
union area 0 - 1 : 4935
240TEST18_final_img.png
240TEST18_dual_img.png
240TEST17_final_img.png
240TEST17_dual_img.png
240TEST10_final_img.png
240TEST10_dual_img.png
240TEST13_final_img.png
240TEST13_dual_img.png
240TEST8_final_img.png
240TEST8_dual_img.png
240TEST23_final_img.png
240TEST23_dual_img.png
240TEST11_final_img.png
240TEST11_dual_img.png
240TEST24_final_img.png
240TEST24_dual_img.png
240TEST1_final_img.png
240TEST1_dual_img.png
240TEST22_final_img.png
240TEST22_dual_img.png
240TEST12_final_img.png
240TEST12_dual_img.png
240TEST25_final_img.png
240TEST25_dual_img.png
240TEST5_final_img.png
240TEST5_dual_img.png
240TEST27_final_img.png
240TEST27_dual_img.png
distance 2 - 3 : 38
union area 2 - 3 : 2785
240TEST20_final_img.png
240TEST20_dual_img.png
240TEST6_final_img.png
240TEST6_dual_img.png
240TEST7_final_img.png
240TEST7_dual_img.png
240TEST21_final_img.png
240TEST

In [3]:
k=1
img = cv2.imread(os.path.join('/home/junhyun/CT_20',file_list[k]))

In [10]:
img.shape

(1520, 2288, 3)

In [7]:
import cv2
import numpy as np
from matplotlib.pyplot import imshow
import os
%matplotlib inline
import csv

In [12]:
def get_intersect_area(comp_A,comp_B):
    A_x, A_y, A_w, A_h = comp_A
    B_x, B_y, B_w, B_h = comp_B
    in_x1 = max(A_x, B_x)
    in_x2 = min(A_x+A_w, B_x+B_w)
    in_w = in_x2 - in_x1

    in_y1 = max(A_y, B_y)
    in_y2 = min(A_y+A_h, B_y+B_h)
    in_h = in_y2 - in_y1

    if (in_w < 0 or in_h < 0):
        interArea = 0
    else:
        interArea = in_w * in_h
        
    return interArea

def get_union_area(comp_A,comp_B):
    A_x, A_y, A_w, A_h = comp_A
    B_x, B_y, B_w, B_h = comp_B
    
    unionArea = A_w * A_h + B_w * B_h - get_intersect_area(comp_A,comp_B)
    
    return unionArea

def get_distance(center_A,center_B):
    A_x, A_y=center_A
    B_x, B_y=center_B
    
    return np.sqrt((A_x-B_x)**2+(A_y-B_y)**2)

def get_marginal_xywh(xywh,margin_wh,image_wh):
    box_x,box_y,box_w,box_h = xywh
    margin_w,margin_h = margin_wh
    img_w,img_h = image_wh
    
    center_x = box_x+box_w/2
    center_y = box_y+box_h/2
    
    x = max(box_x-margin_w,0)
    y = max(box_y-margin_h,0)
    
    if box_x+box_w+margin_w >= img_w:
        w = img_w - x - 1
    else:
        w = box_x+box_w+margin_w - x -1
        
    if box_y+box_h+margin_h >= img_h:
        h = img_h - y -1
    else:
        h = box_y+box_h+margin_h -y -1
    return [int(x),int(y),int(w),int(h)]

In [13]:
# file_list =os.listdir('/home/junhyun/CT_20')
file_list =os.listdir('/home/junhyun/EOS_TEST')


In [18]:
for threshold_value in range(0,255,5):

    for k in range(len(file_list)):
        origin_img = cv2.imread(os.path.join('/home/junhyun/CT_20',file_list[k]))
        img = origin_img[...,::-1].copy()

        img_B = img[:,:,0]
        img_R = img[:,:,2]
        I_1 = img_R-img_B
        
        # threshold_value = 191
        ret, thresh = cv2.threshold(I_1, threshold_value, 255, cv2.THRESH_BINARY)
        I_2 = np.invert(thresh)


        kernel_size_row = 3
        kernel_size_col = 3
        kernel = cv2.getStructuringElement(cv2.MORPH_RECT, (kernel_size_row , kernel_size_col))

        erosion = cv2.erode(I_2,kernel,iterations=1)

        dilation = cv2.dilate(erosion,kernel,iterations=1)

        dilation = cv2.dilate(dilation,kernel,iterations=1)

        ret, dilation = cv2.threshold(dilation, 150, 255, cv2.THRESH_BINARY)

        I_3 = dilation==I_2

        _, contours, _ = cv2.findContours(dilation, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
        
        
        original_img = img.copy()

        center_array = []
        xywh_array=[]

        for cnt in contours:
            area = cv2.contourArea(cnt)

            if area > 20**2:
                x,y,w,h = cv2.boundingRect(cnt)
                cv2.rectangle(original_img, (x,y), (x+w,y+h), (0,255,0), 2)

                center_array.append([x+w/2,y+h/2])
                xywh_array.append([x,y,w,h])
                
        cv2.imwrite(os.path.join('/home/junhyun/TEST_threshold',str(threshold_value)+'_'+os.path.splitext(file_list[k])[0]+"_"+'original_img.png'), original_img)
        
        break_bool =True
        while break_bool:

            max_area = 0
            for x,y,w,h in xywh_array:
                if w*h > max_area:
                    max_area = w*h

            break_bool=False
            for i in range(len(xywh_array)):
                for j in range(i+1,len(xywh_array)):

                    cnt_1_center = [xywh_array[i][0]+xywh_array[i][2]/2,xywh_array[i][1]+xywh_array[i][3]/2]
                    cnt_2_center = [xywh_array[j][0]+xywh_array[j][2]/2,xywh_array[j][1]+xywh_array[j][3]/2]

                    center = [int((cnt_1_center[0]+cnt_2_center[0])/2),int((cnt_1_center[1]+cnt_2_center[1])/2)]

                    distance = get_distance(cnt_1_center,cnt_2_center)
                    union_area = get_union_area(xywh_array[i],xywh_array[j])


                    if (distance<70) and (union_area<=max_area):


                        New_start_x = min(xywh_array[i][0],xywh_array[j][0])
                        New_start_y = min(xywh_array[i][1],xywh_array[j][1])
                        New_end_x = max(xywh_array[i][0],xywh_array[j][0])
                        New_end_y = max(xywh_array[i][1],xywh_array[j][1])

                        New_w = max([center[0]-New_start_x,New_end_x-center[0]])*2
                        New_h = max([center[1]-New_start_y,New_end_y-center[1]])*2

                        xywh = get_marginal_xywh([center[0],center[1],0,0],[New_w/2,New_h/2],[img.shape[1],img.shape[0]])

                        xywh_array.append(xywh)
                        xywh_array.pop(j)
                        xywh_array.pop(i)

                        break_bool = True
                        break
                if break_bool:
                    break
        
        
        final_img = img.copy()
        
        f = open(os.path.join('/home/junhyun/TEST_threshold',str(threshold_value)+"_"+os.path.splitext(file_list[k])[0]+'.csv'), 'w', encoding='utf-8', newline='')
        wr = csv.writer(f)

        for i in range(len(xywh_array)):
            x,y,w,h = xywh_array[i]
            wr.writerow([int(x),int(y),int(w),int(h)])
            img[y:y+h,x:x+w,:] = origin_img[y:y+h,x:x+w,:]
            cv2.rectangle(final_img, (x,y), (x+w,y+h), (0,255,0), 2)
            
        f.close()
        
        cv2.imwrite(os.path.join('/home/junhyun/TEST_threshold',str(threshold_value)+'_'+os.path.splitext(file_list[k])[0]+"_"+'origin_img.png'), origin_img)
        cv2.imwrite(os.path.join('/home/junhyun/TEST_threshold',str(threshold_value)+'_'+os.path.splitext(file_list[k])[0]+"_"+'final_img.png'), final_img)
        print(str(threshold_value)+os.path.splitext(file_list[k])[0]+"_"+'final_img.png')
        

0TEST30_final_img.png
0TEST29_final_img.png
0TEST28_final_img.png
0TEST31_final_img.png
5TEST30_final_img.png
5TEST29_final_img.png
5TEST28_final_img.png
5TEST31_final_img.png
10TEST30_final_img.png
10TEST29_final_img.png
10TEST28_final_img.png
10TEST31_final_img.png
15TEST30_final_img.png
15TEST29_final_img.png
15TEST28_final_img.png
15TEST31_final_img.png
20TEST30_final_img.png
20TEST29_final_img.png
20TEST28_final_img.png
20TEST31_final_img.png
25TEST30_final_img.png
25TEST29_final_img.png
25TEST28_final_img.png
25TEST31_final_img.png
30TEST30_final_img.png
30TEST29_final_img.png
30TEST28_final_img.png
30TEST31_final_img.png
35TEST30_final_img.png
35TEST29_final_img.png
35TEST28_final_img.png
35TEST31_final_img.png
40TEST30_final_img.png
40TEST29_final_img.png
40TEST28_final_img.png
40TEST31_final_img.png
45TEST30_final_img.png
45TEST29_final_img.png
45TEST28_final_img.png
45TEST31_final_img.png
50TEST30_final_img.png
50TEST29_final_img.png
50TEST28_final_img.png
50TEST31_final_img.